In [458]:
import pandas as pd
import os
import hashlib
import pandas as pd
pd.options.mode.chained_assignment = None  # default='warn'
!pip3 install pyproj
from pyproj import Proj, transform
inProj = Proj(init='epsg:28992')
outProj = Proj(init='epsg:4326')

Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com
You should consider upgrading via the '/home/ec2-user/anaconda3/envs/python3/bin/python -m pip install --upgrade pip' command.


/home/ec2-user/anaconda3/envs/python3/lib/python3.8/site-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/home/ec2-user/anaconda3/envs/python3/lib/python3.8/site-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)


In [459]:
data_file_path="~/SageMaker/Rain_Estimation_Using_Loosely_Matched_Stations/Gauges_20110609_20110813.csv"
metadata_file_path = "~/SageMaker/Rain_Estimation_Using_Loosely_Matched_Stations/dutch_gauge_coo.csv"

In [460]:
df = pd.read_csv(data_file_path, sep=",", index_col=False)
metadata_df  = pd.read_csv(metadata_file_path, sep=",", index_col=False)

In [461]:
df[df.RH=="-1"]=0
df.drop(df[df.RH==" "].index,inplace=True)
df.drop(df[df.STN==0].index,inplace=True)

In [462]:
stations=df.STN.unique()
len(stations)

32

In [463]:
df.STN.unique()

array([210, 235, 240, 249, 251, 257, 260, 267, 269, 270, 273, 275, 277,
       278, 279, 280, 283, 286, 290, 310, 319, 323, 330, 344, 348, 350,
       356, 370, 375, 377, 380, 391])

In [464]:
df.to_csv("~/SageMaker/Rain_Estimation_Using_Loosely_Matched_Stations/Gauges_20110609_20110813_temp.csv")

In [465]:
stations

array([210, 235, 240, 249, 251, 257, 260, 267, 269, 270, 273, 275, 277,
       278, 279, 280, 283, 286, 290, 310, 319, 323, 330, 344, 348, 350,
       356, 370, 375, 377, 380, 391])

In [466]:
def convert_from_dutch_coo_to_longitude_latitude(x1,y1):
    return transform(inProj,outProj,x1*1000,y1*1000)

In [467]:
metadata_df=metadata_df.join(metadata_df.apply(lambda x: pd.Series({"long": convert_from_dutch_coo_to_longitude_latitude(x.POS_X, x.POS_Y)[0],
                                       "lat": convert_from_dutch_coo_to_longitude_latitude(x.POS_X, x.POS_Y)[1]}), axis=1))

/tmp/ipykernel_18831/1893588703.py:2: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  return transform(inProj,outProj,x1*1000,y1*1000)


In [468]:
metadata_df.head()

STN    STARTT     STOPT             LOCATIE  HOOGTE  POS_X  POS_Y  POS_NB  \
0  201  20090313  99991231   platform D15-FA-1    42.7   -4.5  707.1    54.3   
1  203  20091109  99991231      platform P11-B    41.8   15.7  487.6    52.4   
2  204  20061206  99991231  platform K14-FA-1C    41.8   37.6  588.3    53.3   
3  205  20090313  99991231    platform A12-CPP    48.4   55.0  825.1    55.4   
4  206  20061206  99991231      platform F16-A    43.4   65.1  682.0    54.1   

   POS_OL      long        lat  
0     2.9  2.936152  54.323898  
1     3.3  3.342154  52.358603  
2     3.6  3.627506  53.268329  
3     3.8  3.809936  55.397968  
4     4.0  4.012695  54.115259

In [469]:
def convert_date(date):
    yyyy=date[:4]
    mm=date[4:6]
    dd=date[6:8]
    return f"{yyyy}-{mm}-{dd}"

def convert_time(time):
    if time=="24":
        hh="00"
    else:
        hh=f"0{time}" if len(time)==1 else f"{time}"
    
    mm="00"
    
    return f"{hh}:{mm}"
    

In [470]:
stations

array([210, 235, 240, 249, 251, 257, 260, 267, 269, 270, 273, 275, 277,
       278, 279, 280, 283, 286, 290, 310, 319, 323, 330, 344, 348, 350,
       356, 370, 375, 377, 380, 391])

In [471]:
df["Time"]=df["YYYYMMDD"].astype(str).apply(convert_date)+" "+df["H"].astype(str).apply(convert_time)
df.RH=df.RH.astype(int)//10 #RH: Hourly precipitation (in 0.1 mm) (-1 for <0.05 mm)
df.rename(columns={"RH": "RainAmout[mm/h]"}, inplace=True)

In [472]:
# for station in stations:
#     df[df.STN==station].apply(lambda x: pd.Series({"Time":convert_datetime_to_time(x.YYYYMMDD,x.H)}
df

STN  YYYYMMDD   H  RainAmout[mm/h]              Time
1584   210  20110609   1                0  2011-06-09 01:00
1585   210  20110609   2                0  2011-06-09 02:00
1586   210  20110609   3                0  2011-06-09 03:00
1587   210  20110609   4                0  2011-06-09 04:00
1588   210  20110609   5                0  2011-06-09 05:00
...    ...       ...  ..              ...               ...
76026  391  20110813  19                0  2011-08-13 19:00
76028  391  20110813  21                0  2011-08-13 21:00
76029  391  20110813  22                0  2011-08-13 22:00
76030  391  20110813  23                0  2011-08-13 23:00
76031  391  20110813  24                0  2011-08-13 00:00

[45485 rows x 5 columns]

In [473]:
def fix_time_representation_for_15_min(datetime):
    global counter
    date,time = datetime.split(' ')
    yyyy,MM,dd = date.split('-')
    hh,mm = time.split(':')
    
    print(counter)
    if counter%4==0:
        mm="00"
    elif counter%4==1:
        mm="15"
    elif counter%4==2:
        mm="30"
    elif counter %4==3:
        mm="45"
        
    counter=counter+1
        
    return f"{dd}-{MM}-{yyyy} {hh}:{mm}"
    

In [475]:
columns=["Time","RainAmout[mm/h]"]
root="~/SageMaker/Rain_Estimation_Using_Loosely_Matched_Stations/CellEnMon/datasets/ims/09062011_13082011/raw"
for station in stations[:]:
    d=df[df.STN==station]
    try:
        long=metadata_df[metadata_df.STN==station].long.iloc[0]
        lat=metadata_df[metadata_df.STN==station].lat.iloc[0]
        d = d.reset_index()
        d.index = pd.to_datetime(d.index, unit="h", origin=pd.Timestamp(d.Time.iloc[0]))
        d=d.resample("15T").ffill()
        counter=0
        d.Time=d.Time.apply(lambda x: fix_time_representation_for_15_min(x))
        d.to_csv(f'{root}/{d.STN.iloc[0]}_{long:.3f}_{lat:.3f}.csv', index=False, columns=columns)
    except IndexError:
        print(f"This station does not exist:{station}")

This station does not exist:210
0
09-06-2011 01:00
1
09-06-2011 01:15
2
09-06-2011 01:30
3
09-06-2011 01:45
4
09-06-2011 02:00
5
09-06-2011 02:15
6
09-06-2011 02:30
7
09-06-2011 02:45
8
09-06-2011 03:00
9
09-06-2011 03:15
10
09-06-2011 03:30
11
09-06-2011 03:45
12
09-06-2011 04:00
13
09-06-2011 04:15
14
09-06-2011 04:30
15
09-06-2011 04:45
16
09-06-2011 05:00
17
09-06-2011 05:15
18
09-06-2011 05:30
19
09-06-2011 05:45
20
09-06-2011 06:00
21
09-06-2011 06:15
22
09-06-2011 06:30
23
09-06-2011 06:45
24
09-06-2011 07:00
25
09-06-2011 07:15
26
09-06-2011 07:30
27
09-06-2011 07:45
28
09-06-2011 08:00
29
09-06-2011 08:15
30
09-06-2011 08:30
31
09-06-2011 08:45
32
09-06-2011 09:00
33
09-06-2011 09:15
34
09-06-2011 09:30
35
09-06-2011 09:45
36
09-06-2011 10:00
37
09-06-2011 10:15
38
09-06-2011 10:30
39
09-06-2011 10:45
40
09-06-2011 11:00
41
09-06-2011 11:15
42
09-06-2011 11:30
43
09-06-2011 11:45
44
09-06-2011 12:00
45
09-06-2011 12:15
46
09-06-2011 12:30
47
09-06-2011 12:45
48
09-06-2011 13:0

26-06-2011 08:00
1501
26-06-2011 08:15
1502
26-06-2011 08:30
1503
26-06-2011 08:45
1504
26-06-2011 09:00
1505
26-06-2011 09:15
1506
26-06-2011 09:30
1507
26-06-2011 09:45
1508
26-06-2011 10:00
1509
26-06-2011 10:15
1510
26-06-2011 10:30
1511
26-06-2011 10:45
1512
26-06-2011 11:00
1513
26-06-2011 11:15
1514
26-06-2011 11:30
1515
26-06-2011 11:45
1516
26-06-2011 12:00
1517
26-06-2011 12:15
1518
26-06-2011 12:30
1519
26-06-2011 12:45
1520
26-06-2011 13:00
1521
26-06-2011 13:15
1522
26-06-2011 13:30
1523
26-06-2011 13:45
1524
26-06-2011 14:00
1525
26-06-2011 14:15
1526
26-06-2011 14:30
1527
26-06-2011 14:45
1528
26-06-2011 15:00
1529
26-06-2011 15:15
1530
26-06-2011 15:30
1531
26-06-2011 15:45
1532
26-06-2011 16:00
1533
26-06-2011 16:15
1534
26-06-2011 16:30
1535
26-06-2011 16:45
1536
26-06-2011 17:00
1537
26-06-2011 17:15
1538
26-06-2011 17:30
1539
26-06-2011 17:45
1540
26-06-2011 18:00
1541
26-06-2011 18:15
1542
26-06-2011 18:30
1543
26-06-2011 18:45
1544
26-06-2011 19:00
1545
26-06-2011

3188
15-07-2011 19:00
3189
15-07-2011 19:15
3190
15-07-2011 19:30
3191
15-07-2011 19:45
3192
15-07-2011 20:00
3193
15-07-2011 20:15
3194
15-07-2011 20:30
3195
15-07-2011 20:45
3196
15-07-2011 21:00
3197
15-07-2011 21:15
3198
15-07-2011 21:30
3199
15-07-2011 21:45
3200
15-07-2011 22:00
3201
15-07-2011 22:15
3202
15-07-2011 22:30
3203
15-07-2011 22:45
3204
15-07-2011 23:00
3205
15-07-2011 23:15
3206
15-07-2011 23:30
3207
15-07-2011 23:45
3208
15-07-2011 00:00
3209
15-07-2011 00:15
3210
15-07-2011 00:30
3211
15-07-2011 00:45
3212
16-07-2011 01:00
3213
16-07-2011 01:15
3214
16-07-2011 01:30
3215
16-07-2011 01:45
3216
16-07-2011 02:00
3217
16-07-2011 02:15
3218
16-07-2011 02:30
3219
16-07-2011 02:45
3220
16-07-2011 03:00
3221
16-07-2011 03:15
3222
16-07-2011 03:30
3223
16-07-2011 03:45
3224
16-07-2011 04:00
3225
16-07-2011 04:15
3226
16-07-2011 04:30
3227
16-07-2011 04:45
3228
16-07-2011 05:00
3229
16-07-2011 05:15
3230
16-07-2011 05:30
3231
16-07-2011 05:45
3232
16-07-2011 08:00
3233
16-07

4934
05-08-2011 03:30
4935
05-08-2011 03:45
4936
05-08-2011 04:00
4937
05-08-2011 04:15
4938
05-08-2011 04:30
4939
05-08-2011 04:45
4940
05-08-2011 05:00
4941
05-08-2011 05:15
4942
05-08-2011 05:30
4943
05-08-2011 05:45
4944
05-08-2011 06:00
4945
05-08-2011 06:15
4946
05-08-2011 06:30
4947
05-08-2011 06:45
4948
05-08-2011 07:00
4949
05-08-2011 07:15
4950
05-08-2011 07:30
4951
05-08-2011 07:45
4952
05-08-2011 08:00
4953
05-08-2011 08:15
4954
05-08-2011 08:30
4955
05-08-2011 08:45
4956
05-08-2011 09:00
4957
05-08-2011 09:15
4958
05-08-2011 09:30
4959
05-08-2011 09:45
4960
05-08-2011 10:00
4961
05-08-2011 10:15
4962
05-08-2011 10:30
4963
05-08-2011 10:45
4964
05-08-2011 11:00
4965
05-08-2011 11:15
4966
05-08-2011 11:30
4967
05-08-2011 11:45
4968
05-08-2011 12:00
4969
05-08-2011 12:15
4970
05-08-2011 12:30
4971
05-08-2011 12:45
4972
05-08-2011 13:00
4973
05-08-2011 13:15
4974
05-08-2011 13:30
4975
05-08-2011 13:45
4976
05-08-2011 14:00
4977
05-08-2011 14:15
4978
05-08-2011 14:30
4979
05-08

799
18-06-2011 13:45
800
18-06-2011 14:00
801
18-06-2011 14:15
802
18-06-2011 14:30
803
18-06-2011 14:45
804
18-06-2011 15:00
805
18-06-2011 15:15
806
18-06-2011 15:30
807
18-06-2011 15:45
808
18-06-2011 16:00
809
18-06-2011 16:15
810
18-06-2011 16:30
811
18-06-2011 16:45
812
18-06-2011 17:00
813
18-06-2011 17:15
814
18-06-2011 17:30
815
18-06-2011 17:45
816
18-06-2011 18:00
817
18-06-2011 18:15
818
18-06-2011 18:30
819
18-06-2011 18:45
820
18-06-2011 19:00
821
18-06-2011 19:15
822
18-06-2011 19:30
823
18-06-2011 19:45
824
18-06-2011 21:00
825
18-06-2011 21:15
826
18-06-2011 21:30
827
18-06-2011 21:45
828
18-06-2011 22:00
829
18-06-2011 22:15
830
18-06-2011 22:30
831
18-06-2011 22:45
832
18-06-2011 23:00
833
18-06-2011 23:15
834
18-06-2011 23:30
835
18-06-2011 23:45
836
18-06-2011 00:00
837
18-06-2011 00:15
838
18-06-2011 00:30
839
18-06-2011 00:45
840
19-06-2011 01:00
841
19-06-2011 01:15
842
19-06-2011 01:30
843
19-06-2011 01:45
844
19-06-2011 02:00
845
19-06-2011 02:15
846
19-06-201

...

10-07-2011 03:15
2682
10-07-2011 03:30
2683
10-07-2011 03:45
2684
10-07-2011 04:00
2685
10-07-2011 04:15
2686
10-07-2011 04:30
2687
10-07-2011 04:45
2688
10-07-2011 05:00
2689
10-07-2011 05:15
2690
10-07-2011 05:30
2691
10-07-2011 05:45
2692
10-07-2011 06:00
2693
10-07-2011 06:15
2694
10-07-2011 06:30
2695
10-07-2011 06:45
2696
10-07-2011 07:00
2697
10-07-2011 07:15
2698
10-07-2011 07:30
2699
10-07-2011 07:45
2700
10-07-2011 08:00
2701
10-07-2011 08:15
2702
10-07-2011 08:30
2703
10-07-2011 08:45
2704
10-07-2011 09:00
2705
10-07-2011 09:15
2706
10-07-2011 09:30
2707
10-07-2011 09:45
2708
10-07-2011 10:00
2709
10-07-2011 10:15
2710
10-07-2011 10:30
2711
10-07-2011 10:45
2712
10-07-2011 11:00
2713
10-07-2011 11:15
2714
10-07-2011 11:30
2715
10-07-2011 11:45
2716
10-07-2011 12:00
2717
10-07-2011 12:15
2718
10-07-2011 12:30
2719
10-07-2011 12:45
2720
10-07-2011 13:00
2721
10-07-2011 13:15
2722
10-07-2011 13:30
2723
10-07-2011 13:45
2724
10-07-2011 16:00
2725
10-07-2011 16:15
2726
10-07-2011

02-08-2011 07:00
4641
02-08-2011 07:15
4642
02-08-2011 07:30
4643
02-08-2011 07:45
4644
02-08-2011 08:00
4645
02-08-2011 08:15
4646
02-08-2011 08:30
4647
02-08-2011 08:45
4648
02-08-2011 09:00
4649
02-08-2011 09:15
4650
02-08-2011 09:30
4651
02-08-2011 09:45
4652
02-08-2011 10:00
4653
02-08-2011 10:15
4654
02-08-2011 10:30
4655
02-08-2011 10:45
4656
02-08-2011 11:00
4657
02-08-2011 11:15
4658
02-08-2011 11:30
4659
02-08-2011 11:45
4660
02-08-2011 12:00
4661
02-08-2011 12:15
4662
02-08-2011 12:30
4663
02-08-2011 12:45
4664
02-08-2011 13:00
4665
02-08-2011 13:15
4666
02-08-2011 13:30
4667
02-08-2011 13:45
4668
02-08-2011 14:00
4669
02-08-2011 14:15
4670
02-08-2011 14:30
4671
02-08-2011 14:45
4672
02-08-2011 15:00
4673
02-08-2011 15:15
4674
02-08-2011 15:30
4675
02-08-2011 15:45
4676
02-08-2011 16:00
4677
02-08-2011 16:15
4678
02-08-2011 16:30
4679
02-08-2011 16:45
4680
02-08-2011 17:00
4681
02-08-2011 17:15
4682
02-08-2011 17:30
4683
02-08-2011 17:45
4684
02-08-2011 18:00
4685
02-08-2011

515
14-06-2011 13:45
516
14-06-2011 14:00
517
14-06-2011 14:15
518
14-06-2011 14:30
519
14-06-2011 14:45
520
14-06-2011 15:00
521
14-06-2011 15:15
522
14-06-2011 15:30
523
14-06-2011 15:45
524
14-06-2011 16:00
525
14-06-2011 16:15
526
14-06-2011 16:30
527
14-06-2011 16:45
528
14-06-2011 17:00
529
14-06-2011 17:15
530
14-06-2011 17:30
531
14-06-2011 17:45
532
14-06-2011 18:00
533
14-06-2011 18:15
534
14-06-2011 18:30
535
14-06-2011 18:45
536
14-06-2011 19:00
537
14-06-2011 19:15
538
14-06-2011 19:30
539
14-06-2011 19:45
540
14-06-2011 20:00
541
14-06-2011 20:15
542
14-06-2011 20:30
543
14-06-2011 20:45
544
14-06-2011 21:00
545
14-06-2011 21:15
546
14-06-2011 21:30
547
14-06-2011 21:45
548
14-06-2011 22:00
549
14-06-2011 22:15
550
14-06-2011 22:30
551
14-06-2011 22:45
552
14-06-2011 23:00
553
14-06-2011 23:15
554
14-06-2011 23:30
555
14-06-2011 23:45
556
14-06-2011 00:00
557
14-06-2011 00:15
558
14-06-2011 00:30
559
14-06-2011 00:45
560
15-06-2011 01:00
561
15-06-2011 01:15
562
15-06-201

06-07-2011 20:45
2568
06-07-2011 21:00
2569
06-07-2011 21:15
2570
06-07-2011 21:30
2571
06-07-2011 21:45
2572
06-07-2011 22:00
2573
06-07-2011 22:15
2574
06-07-2011 22:30
2575
06-07-2011 22:45
2576
06-07-2011 23:00
2577
06-07-2011 23:15
2578
06-07-2011 23:30
2579
06-07-2011 23:45
2580
06-07-2011 00:00
2581
06-07-2011 00:15
2582
06-07-2011 00:30
2583
06-07-2011 00:45
2584
07-07-2011 01:00
2585
07-07-2011 01:15
2586
07-07-2011 01:30
2587
07-07-2011 01:45
2588
07-07-2011 02:00
2589
07-07-2011 02:15
2590
07-07-2011 02:30
2591
07-07-2011 02:45
2592
07-07-2011 03:00
2593
07-07-2011 03:15
2594
07-07-2011 03:30
2595
07-07-2011 03:45
2596
07-07-2011 04:00
2597
07-07-2011 04:15
2598
07-07-2011 04:30
2599
07-07-2011 04:45
2600
07-07-2011 05:00
2601
07-07-2011 05:15
2602
07-07-2011 05:30
2603
07-07-2011 05:45
2604
07-07-2011 06:00
2605
07-07-2011 06:15
2606
07-07-2011 06:30
2607
07-07-2011 06:45
2608
07-07-2011 07:00
2609
07-07-2011 07:15
2610
07-07-2011 07:30
2611
07-07-2011 07:45
2612
07-07-2011

4411
26-07-2011 21:45
4412
26-07-2011 22:00
4413
26-07-2011 22:15
4414
26-07-2011 22:30
4415
26-07-2011 22:45
4416
26-07-2011 23:00
4417
26-07-2011 23:15
4418
26-07-2011 23:30
4419
26-07-2011 23:45
4420
26-07-2011 00:00
4421
26-07-2011 00:15
4422
26-07-2011 00:30
4423
26-07-2011 00:45
4424
27-07-2011 01:00
4425
27-07-2011 01:15
4426
27-07-2011 01:30
4427
27-07-2011 01:45
4428
27-07-2011 02:00
4429
27-07-2011 02:15
4430
27-07-2011 02:30
4431
27-07-2011 02:45
4432
27-07-2011 03:00
4433
27-07-2011 03:15
4434
27-07-2011 03:30
4435
27-07-2011 03:45
4436
27-07-2011 04:00
4437
27-07-2011 04:15
4438
27-07-2011 04:30
4439
27-07-2011 04:45
4440
27-07-2011 05:00
4441
27-07-2011 05:15
4442
27-07-2011 05:30
4443
27-07-2011 05:45
4444
27-07-2011 07:00
4445
27-07-2011 07:15
4446
27-07-2011 07:30
4447
27-07-2011 07:45
4448
27-07-2011 08:00
4449
27-07-2011 08:15
4450
27-07-2011 08:30
4451
27-07-2011 08:45
4452
27-07-2011 09:00
4453
27-07-2011 09:15
4454
27-07-2011 09:30
4455
27-07-2011 09:45
4456
27-07

In [476]:
a=[1,2,3,4,5,6,7,8]
a[::1]

[1, 2, 3, 4, 5, 6, 7, 8]